In [165]:
import bt
import backtesting
import pandas as pd
from tqdm import tqdm
import numpy as np
import FinanceDataReader as fdr

### 1. Data Uploading

In [2]:
data_path = '/Users/ljhee/Desktop/BOAZ/Fintshift/Data/'

# 각 투자 유형 내 주식들의 종가 데이터
# column : 주식 / row : 2016년 1월 4일 - 2023년 9월 27일
price_stable_final = pd.read_csv(f'{data_path}안정성_주가_백테스트용.csv')
price_value_final = pd.read_csv(f'{data_path}가치성_주가_백테스트용.csv')
price_grow_final = pd.read_csv(f'{data_path}성장성_주가_백테스트용.csv')
price_cost_final = pd.read_csv(f'{data_path}수익성_주가_백테스트용.csv')

# 전체 주식의 종가 데이터 -> 개별 주식을 컬럼으로 설정
df = pd.concat([price_stable_final,price_value_final,price_grow_final,price_cost_final],axis=1)

In [5]:
# 각 주식의 종가 데이터
cost = pd.read_csv(f"{data_path}15_23_주가데이터_1201.csv")

cost['stock_code'] =  [str(num).zfill(6) for num in cost['stock_code']]

#### 주가 데이터 16년도부터로 변경
date = cost['Date'].str.split('-')
idx=[]
for i,d in enumerate(date):
     if d[0] != '2015':
        idx.append(i)

cost = cost.iloc[idx,:]

/Users/ljhee/opt/anaconda3/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3444: DtypeWarning: Columns (0) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [10]:
data = pd.read_csv(f'{data_path}주식별_수익률.csv')
new_row = pd.Series({'Date': '2016-01-03'})
temp = cost[cost['stock_code']=='000020']['Date']
temp.loc[247] = '2016-01-03'
temp.sort_index(inplace=True)
data.index = temp.apply(pd.to_datetime)
# data.index = pd.to_datetime(data.index)

/Users/ljhee/opt/anaconda3/lib/python3.9/site-packages/pandas/core/indexing.py:1724: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer_missing(indexer, value)
/Users/ljhee/opt/anaconda3/lib/python3.9/site-packages/pandas/core/generic.py:4567: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return self._update_inplace(result)


In [8]:
# 투자 유형별로 주식을 분리 -> 추후 Type Score별로 내림차순 정렬해야 해서 해당 데이터 사용
stock = pd.read_excel(f'{data_path}6_dartdata_stocktype_1222.xlsx')

df_stable = stock[stock['type']=='안정성']
df_value = stock[stock['type']=='가치성']
df_grow = stock[stock['type']=='성장성']
df_cost = stock[stock['type']=='수익성']

In [70]:
# 기준 ETF : kodex200
price_df = fdr.DataReader('069500')
kodex200 = price_df['2016-01-04':][['Close']]

In [21]:
_stock = pd.read_excel(f'{data_path}2_dartdata_variable_1222.xlsx')
_stock = _stock[['종목코드','종목명']]
_stock.drop_duplicates(inplace=True)
stock_dic = dict(zip(_stock['종목코드'], _stock['종목명']))

### 2. Creating functions for your own ETF

Using BT Library

In [68]:
def buy_and_hold(data, name):

    # 벤치마크 전략 생성
    bt_strategy = bt.Strategy(name, [
        bt.algos.SelectAll(),
        bt.algos.WeighEqually(), #same weight
        bt.algos.RunOnce(),
        bt.algos.Rebalance(),
    ])
    # Return the backtest
    return bt.Backtest(bt_strategy, data)

In [12]:
def buy_and_hold_weight(data, name, dic):

    # 벤치마크 전략 생성
    bt_strategy = bt.Strategy(name, [
        bt.algos.SelectAll(),
        bt.algos.WeighSpecified(**dic), 
        bt.algos.RunOnce(),
        bt.algos.Rebalance(),
    ])
    # Return the backtest
    return bt.Backtest(bt_strategy, data)

In [72]:
def sameweight_benchmark(data,test):
    # 벤치마크 전략 백테스트

    kodex200_bench = buy_and_hold(kodex200, name='kodex')
    type_port = buy_and_hold(data[test], name='type') #same weight

    bt_sma_result = bt.run(type_port,kodex200_bench) 
    
    return bt_sma_result.prices.to_returns(), bt_sma_result.get_security_weights()

In [117]:
def diffweight_benchmark(data,test,type_dic):
    # 벤치마크 전략 백테스트

    kodex200_bench = buy_and_hold(kodex200, name='kodex')
    type_port = buy_and_hold_weight(data[test], name='type',dic = type_dic) #dic : ETF 구성종목들의 초기일자 구성비율

    bt_sma_result = bt.run(type_port,kodex200_bench)
    
    return bt_sma_result.prices.to_returns(), bt_sma_result.get_security_weights()

In [113]:
def preprocessing(etf_res,etf_weight,stock_dic,top,etf_name):
    
    time = list(etf_weight.index)
    etf_weight = pd.melt(etf_weight)
    etf_weight['time'] = time*top

    time = list(etf_res.index)
    etf_res = pd.melt(etf_res)
    etf_res['time'] = time*2

    etf_res.columns = ['주식유형','수익률','시점']
    etf_weight.columns = ['종목명','자산별_비중','시점']

    etf_weight['종목명'] = etf_weight['종목명'].map(stock_dic)

    etf_res['ETF'] = etf_name
    etf_weight['ETF'] = etf_name
    
    return etf_res,etf_weight

In [135]:
def make_etf(df,data,top,score,weight,stock_type,stock_dic,etf_name):
    sort_name = (df.sort_values(by=score,ascending=False).head(top)['종목코드'])
    sort_df = df.sort_values(by=score,ascending=False).head(top)
    #종목별 TOP 10
    sort_df['scale_score'] = sort_df[score]/sum(sort_df[score])
    sort_df_dic = dict([x for x in zip(sort_df['종목코드'],sort_df['scale_score'])])

    if weight == 'same':
        etf_res, etf_weight = sameweight_benchmark(data,sort_name)
    elif weight == 'diff':
        etf_res, etf_weight = diffweight_benchmark(data,sort_name,sort_df_dic)

    etf_res.columns = [stock_type, 'kodex200']
    
    etf_res, etf_weight = preprocessing(etf_res, etf_weight,stock_dic,top,etf_name)
    etf_weight['주식유형'] = stock_type
    
    return etf_res, etf_weight

### 3. Making ETF

#### 3.1 HAUL_유형별 점수_ETF

In [160]:
###### 1. HAUL_유형별 점수_Top10_동일가중 ######
haul_ts_top10_same_stable, haul_ts_top10_same_stable_weight = make_etf(df_stable,data,10,'type_score','same','안정성',stock_dic,'HAUL_유형별 점수_Top10_동일가중')
haul_ts_top10_same_value, haul_ts_top10_same_value_weight = make_etf(df_value,data,10,'type_score','same','가치성',stock_dic,'HAUL_유형별 점수_Top10_동일가중')
haul_ts_top10_same_grow, haul_ts_top10_same_grow_weight = make_etf(df_grow,data,10,'type_score','same','성장성',stock_dic,'HAUL_유형별 점수_Top10_동일가중')
haul_ts_top10_same_cost, haul_ts_top10_same_cost_weight = make_etf(df_cost,data,10,'type_score','same','수익성',stock_dic,'HAUL_유형별 점수_Top10_동일가중')

haul_ts_top10_same = pd.concat([haul_ts_top10_same_stable,haul_ts_top10_same_value,haul_ts_top10_same_grow,haul_ts_top10_same_cost],axis=0)
haul_ts_top10_same_weight = pd.concat([haul_ts_top10_same_stable_weight,haul_ts_top10_same_value_weight,haul_ts_top10_same_grow_weight,haul_ts_top10_same_cost_weight],axis=0)

haul_ts_top10_same['ETF_대분류'] = '동일가중'; haul_ts_top10_same['ETF_설명'] = '유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)'
haul_ts_top10_same_weight['ETF_대분류'] = '동일가중'; haul_ts_top10_same_weight['ETF_설명'] = '유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)'

###### 2. HAUL_유형별 점수_Top200_동일가중 ######
haul_ts_top200_same_stable, haul_ts_top200_same_stable_weight = make_etf(df_stable,data,200,'type_score','same','안정성',stock_dic,'HAUL_유형별 점수_Top200_동일가중')
haul_ts_top200_same_value, haul_ts_top200_same_value_weight = make_etf(df_value,data,200,'type_score','same','가치성',stock_dic,'HAUL_유형별 점수_Top200_동일가중')
haul_ts_top200_same_grow, haul_ts_top200_same_grow_weight = make_etf(df_grow,data,200,'type_score','same','성장성',stock_dic,'HAUL_유형별 점수_Top200_동일가중')
haul_ts_top200_same_cost, haul_ts_top200_same_cost_weight = make_etf(df_cost,data,200,'type_score','same','수익성',stock_dic,'HAUL_유형별 점수_Top200_동일가중')

haul_ts_top200_same = pd.concat([haul_ts_top200_same_stable,haul_ts_top200_same_value,haul_ts_top200_same_grow,haul_ts_top200_same_cost],axis=0)
haul_ts_top200_same_weight = pd.concat([haul_ts_top200_same_stable_weight,haul_ts_top200_same_value_weight,haul_ts_top200_same_grow_weight,haul_ts_top200_same_cost_weight],axis=0)

haul_ts_top200_same['ETF_대분류'] = '동일가중'; haul_ts_top200_same['ETF_설명'] = '유형별 점수 상위 200개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)'
haul_ts_top200_same_weight['ETF_대분류'] = '동일가중'; haul_ts_top200_same_weight['ETF_설명'] = '유형별 점수 상위 200개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)'

###### 3. HAUL_유형별 점수_Top10_상이가중 ######
haul_ts_top10_diff_stable, haul_ts_top10_diff_stable_weight = make_etf(df_stable,data,10,'type_score','diff','안정성',stock_dic,'HAUL_유형별 점수_Top10_상이가중')
haul_ts_top10_diff_value, haul_ts_top10_diff_value_weight = make_etf(df_value,data,10,'type_score','diff','가치성',stock_dic,'HAUL_유형별 점수_Top10_상이가중')
haul_ts_top10_diff_grow, haul_ts_top10_diff_grow_weight = make_etf(df_grow,data,10,'type_score','diff','성장성',stock_dic,'HAUL_유형별 점수_Top10_상이가중')
haul_ts_top10_diff_cost, haul_ts_top10_diff_cost_weight = make_etf(df_cost,data,10,'type_score','diff','수익성',stock_dic,'HAUL_유형별 점수_Top10_상이가중')

haul_ts_top10_diff = pd.concat([haul_ts_top10_diff_stable,haul_ts_top10_diff_value,haul_ts_top10_diff_grow,haul_ts_top10_diff_cost],axis=0)
haul_ts_top10_diff_weight = pd.concat([haul_ts_top10_diff_stable_weight,haul_ts_top10_diff_value_weight,haul_ts_top10_diff_grow_weight,haul_ts_top10_diff_cost_weight],axis=0)

haul_ts_top10_diff['ETF_대분류'] = '상이가중'; haul_ts_top10_diff['ETF_설명'] = '유형별 점수 상위 10개 종목을 상이 가중 방식으로 편입한 ETF입니다. (유형 선택)'
haul_ts_top10_diff_weight['ETF_대분류'] = '상이가중'; haul_ts_top10_diff_weight['ETF_설명'] = '유형별 점수 상위 10개 종목을 상이 가중 방식으로 편입한 ETF입니다. (유형 선택)'

###### 4. HAUL_유형별 점수_Top200_상이가중 ######
haul_ts_top200_diff_stable, haul_ts_top200_diff_stable_weight = make_etf(df_stable,data,200,'type_score','diff','안정성',stock_dic,'HAUL_유형별 점수_Top200_상이가중')
haul_ts_top200_diff_value, haul_ts_top200_diff_value_weight = make_etf(df_value,data,200,'type_score','diff','가치성',stock_dic,'HAUL_유형별 점수_Top200_상이가중')
haul_ts_top200_diff_grow, haul_ts_top200_diff_grow_weight = make_etf(df_stable,data,200,'type_score','diff','성장성',stock_dic,'HAUL_유형별 점수_Top200_상이가중')
haul_ts_top200_diff_cost, haul_ts_top200_diff_cost_weight = make_etf(df_cost,data,200,'type_score','diff','수익성',stock_dic,'HAUL_유형별 점수_Top200_상이가중')

haul_ts_top200_diff = pd.concat([haul_ts_top200_diff_stable,haul_ts_top200_diff_value,haul_ts_top200_diff_grow,haul_ts_top200_diff_cost],axis=0)
haul_ts_top200_diff_weight = pd.concat([haul_ts_top200_diff_stable_weight,haul_ts_top200_diff_value_weight,haul_ts_top200_diff_grow_weight,haul_ts_top200_diff_cost_weight],axis=0)

haul_ts_top200_diff['ETF_대분류'] = '상이가중'; haul_ts_top200_diff['ETF_설명'] = '유형별 점수 상위 200개 종목을 상이 가중 방식으로 편입한 ETF입니다. (유형 선택)'
haul_ts_top200_diff_weight['ETF_대분류'] = '상이가중'; haul_ts_top200_diff_weight['ETF_설명'] = '유형별 점수 상위 200개 종목을 상이 가중 방식으로 편입한 ETF입니다. (유형 선택)'

###### 5. HAUL_유형 합계 점수_Top10_동일가중 ######
haul_fs_top10_same, haul_fs_top10_same_weight = make_etf(stock,data,10,'final_score','same','전체',stock_dic,'HAUL_유형 합계 점수_Top10_동일가중')

haul_fs_top10_same['ETF_대분류'] = '동일가중'; haul_fs_top10_same['ETF_설명'] = '유형 합계 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다.'
haul_fs_top10_same_weight['ETF_대분류'] = '동일가중'; haul_fs_top10_same_weight['ETF_설명'] = '유형 합계 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다.'

###### 6. HAUL_유형 합계 점수_Top200_동일가중 ######
haul_fs_top200_same, haul_fs_top200_same_weight = make_etf(stock,data,200,'final_score','same','전체',stock_dic,'HAUL_유형 합계 점수_Top200_동일가중')

haul_fs_top200_same['ETF_대분류'] = '동일가중'; haul_fs_top200_same['ETF_설명'] = '유형 합계 점수 상위 200개 종목을 동일 가중 방식으로 편입한 ETF입니다.'
haul_fs_top200_same_weight['ETF_대분류'] = '동일가중'; haul_fs_top200_same_weight['ETF_설명'] = '유형 합계 점수 상위 200개 종목을 동일 가중 방식으로 편입한 ETF입니다.'

###### 7. HAUL_유형 합계 점수_Top10_상이가중 ######
haul_fs_top10_diff, haul_fs_top10_diff_weight = make_etf(stock,data,10,'final_score','diff','전체',stock_dic,'HAUL_유형 합계 점수_Top10_상이가중')

haul_fs_top10_diff['ETF_대분류'] = '상이가중'; haul_fs_top10_diff['ETF_설명'] = '유형 합계 점수 상위 10개 종목을 상이 가중 방식으로 편입한 ETF입니다.'
haul_fs_top200_same_weight['ETF_대분류'] = '상이가중'; haul_fs_top200_same_weight['ETF_설명'] = '유형 합계 점수 상위 10개 종목을 상이 가중 방식으로 편입한 ETF입니다.'

###### 8. HAUL_유형별 점수_Top200_상이가중 ######
haul_fs_top200_diff, haul_fs_top200_diff_weight = make_etf(stock,data,200,'final_score','diff','전체',stock_dic,'HAUL_유형 합계 점수_Top200_상이가중')

haul_fs_top200_diff['ETF_대분류'] = '상이가중'; haul_fs_top200_diff['ETF_설명'] = '유형 합계 점수 상위 200개 종목을 상이 가중 방식으로 편입한 ETF입니다.'
haul_fs_top200_diff_weight['ETF_대분류'] = '상이가중'; haul_fs_top200_diff_weight['ETF_설명'] = '유형 합계 점수 상위 200개 종목을 상이 가중 방식으로 편입한 ETF입니다.'

In [164]:
etf_df = pd.concat([haul_ts_top10_same,haul_ts_top200_same,haul_ts_top10_diff,haul_ts_top200_diff,haul_fs_top10_same,haul_fs_top200_same,haul_fs_top10_diff,haul_fs_top200_diff],axis=0)

etf_weight = pd.concat([haul_ts_top10_same_weight,haul_ts_top200_same_weight,haul_ts_top10_diff_weight,haul_ts_top200_diff_weight,
                        haul_fs_top10_same_weight,haul_fs_top200_same_weight,haul_fs_top10_diff_weight,haul_fs_top200_diff_weight],axis=0)

etf_df.to_csv(f'{data_path}백테스팅_보유형_ver1.csv',index=False)
etf_weight.to_csv(f'{data_path}백테스팅_보유형_자산별가중치.csv',index=False)

',주식유형,수익률,시점,ETF,ETF_대분류,ETF_설명\n0,안정성,,2016-01-03,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n1,안정성,0.0,2016-01-04,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n2,안정성,0.008809099999999903,2016-01-05,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n3,안정성,0.00878877876894646,2016-01-06,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n4,안정성,-0.0007351067673551093,2016-01-07,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n5,안정성,-0.0015121043079582286,2016-01-08,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n6,안정성,-0.013289284555335734,2016-01-11,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n7,안정성,0.026199633355048935,2016-01-12,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 점수 상위 10개 종목을 동일 가중 방식으로 편입한 ETF입니다. (유형 선택)\n8,안정성,-0.010702867786158587,2016-01-13,HAUL_유형별 점수_Top10_동일가중,동일가중,유형별 